<a href="https://colab.research.google.com/github/laynejohnson13/ahi-competition/blob/main/507_comp.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import pandas as pd

In [2]:
!pip install tpot mljar-supervised

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 87 kB 1.8 MB/s 
     |████████████████████████████████| 112 kB 7.4 MB/s 
     |████████████████████████████████| 139 kB 17.9 MB/s 
     |████████████████████████████████| 193.6 MB 58 kB/s 
     |████████████████████████████████| 2.0 MB 43.3 MB/s 
     |████████████████████████████████| 76.6 MB 1.2 MB/s 
     |████████████████████████████████| 72 kB 963 kB/s 
     |████████████████████████████████| 575 kB 64.6 MB/s 
     |████████████████████████████████| 72 kB 855 kB/s 
     |████████████████████████████████| 348 kB 84.5 MB/s 
     |████████████████████████████████| 209 kB 74.7 MB/s 
     |████████████████████████████████| 81 kB 9.9 MB/s 
     |████████████████████████████████| 78 kB 7.9 MB/s 
     |████████████████████████████████| 147 kB 76.7 MB/s 
     |████████████████████████████████| 50 kB 6.3 MB/s 
     |████████████████████████████████| 112 

In [3]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML

In [4]:
df = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/competition/data/output_noshow1_balanced_2022-11-16.csv')
df

id   patient_id_2  practice_id  appointment_id  patient_id  \
0      1203271  325507_289930       325507         2661965      289930   
1       739988  303801_600804       303801         3135811      600804   
2       988588  325504_140961       325504          632551      140961   
3       511872  303202_271430       303202         1397209      271430   
4       906441  325502_320693       325502         2073212      320693   
...        ...            ...          ...             ...         ...   
99995  1112084  325505_339215       325505         2155885      339215   
99996   664096  303801_589658       303801         3069414      589658   
99997   551566  303205_270436       303205         1969680      270436   
99998  1277662  325508_345572       325508         2283897      345572   
99999  1441361   325512_46926       325512          696690       46926   

      appointment_date appointment_start_time  appointment_duration  \
0           2021-01-11               18:30:00                     5   
1           2020-07-14               12:30:00                    15   
2           2020-05-14               10:32:00                    10   
3           2020-06-24               14:10:00                    20   
4           2021-03-09               17:40:00                    10   
...                ...                    ...                   ...   
99995       2021-07-09               17:40:00                    10   
99996       2019-09-26               10:30:00                    15   
99997       2021-07-20               14:30:00                    15   
99998       2021-10-02               14:00:00                    10   
99999       2020-07-30               15:10:00                     5   

             appointment_type appointment_status  ... geocode_county  \
0         Rapid-COVID Antigen                  x  ...            NaN   
1                         GYN                  4  ...            NaN   
2             CLINICIAN VISIT                  4  ...            NaN   
3                  WELL CHECK                  x  ...            NaN   
4             CLINICIAN VISIT                  4  ...            NaN   
...                       ...                ...  ...            ...   
99995         CLINICIAN VISIT                  x  ...            NaN   
99996                  Annual                  x  ...            NaN   
99997  Established Sick Visit                  x  ...            NaN   
99998         CLINICIAN VISIT                  x  ...            NaN   
99999                 TELEMED                  x  ...            NaN   

      geocode_state geocode_stusab geocode_latitude geocode_longitude  \
0               NaN            NaN              NaN               NaN   
1               NaN            NaN              NaN               NaN   
2               NaN            NaN              NaN               NaN   
3               NaN            NaN              NaN               NaN   
4               NaN            NaN              NaN               NaN   
...             ...            ...              ...               ...   
99995           NaN            NaN              NaN               NaN   
99996           NaN            NaN              NaN               NaN   
99997           NaN            NaN              NaN               NaN   
99998           NaN            NaN              NaN               NaN   
99999           NaN            NaN              NaN               NaN   

       geocode_lengthlife  geocode_healthybehaviors geocode_clinicalcare  \
0                     NaN                       NaN                  NaN   
1                     NaN                       NaN                  NaN   
2                     NaN                       NaN                  NaN   
3                     NaN                       NaN                  NaN   
4                     NaN                       NaN                  NaN   
...                   ...                       ...                  ...

In [5]:
df.columns

Index(['id', 'patient_id_2', 'practice_id', 'appointment_id', 'patient_id',
       'appointment_date', 'appointment_start_time', 'appointment_duration',
       'appointment_type', 'appointment_status', 'appointment_date_time',
       'appointment_last_modified_date', 'appointment_scheduled_date',
       'appointment_yosi_noshow1', 'appointment_yosi_noshow2', 'custom_client',
       'custom_client_site', 'client_site', 'patient_dob', 'patient_zipcode_x',
       'patient_gender', 'patient_age', 'data_collect', 'patient_age_groupper',
       'appointment_date_qt', 'appointment_date_month',
       'appointment_date_year', 'appintmentWithin3DayHoliday',
       'appintmentWithin5DayHoliday', 'appintmentWithin7DayHoliday',
       'appointment_start_time_groupper', 'appointment_start_time_hour',
       'zipcode', 'weather_conditions', 'weather_icon', 'geocode_zip',
       'geocode_city', 'geocode_county', 'geocode_state', 'geocode_stusab',
       'geocode_latitude', 'geocode_longitude', 'geoco

In [6]:
df['appointment_yosi_noshow1'].describe()

count     100000
unique         2
top            N
freq       50000
Name: appointment_yosi_noshow1, dtype: object

In [11]:
x = df.drop(columns=['appointment_yosi_noshow1'])
y = df['appointment_yosi_noshow1']

In [12]:
x

id   patient_id_2  practice_id  appointment_id  patient_id  \
0      1203271  325507_289930       325507         2661965      289930   
1       739988  303801_600804       303801         3135811      600804   
2       988588  325504_140961       325504          632551      140961   
3       511872  303202_271430       303202         1397209      271430   
4       906441  325502_320693       325502         2073212      320693   
...        ...            ...          ...             ...         ...   
99995  1112084  325505_339215       325505         2155885      339215   
99996   664096  303801_589658       303801         3069414      589658   
99997   551566  303205_270436       303205         1969680      270436   
99998  1277662  325508_345572       325508         2283897      345572   
99999  1441361   325512_46926       325512          696690       46926   

      appointment_date appointment_start_time  appointment_duration  \
0           2021-01-11               18:30:00                     5   
1           2020-07-14               12:30:00                    15   
2           2020-05-14               10:32:00                    10   
3           2020-06-24               14:10:00                    20   
4           2021-03-09               17:40:00                    10   
...                ...                    ...                   ...   
99995       2021-07-09               17:40:00                    10   
99996       2019-09-26               10:30:00                    15   
99997       2021-07-20               14:30:00                    15   
99998       2021-10-02               14:00:00                    10   
99999       2020-07-30               15:10:00                     5   

             appointment_type appointment_status  ... geocode_county  \
0         Rapid-COVID Antigen                  x  ...            NaN   
1                         GYN                  4  ...            NaN   
2             CLINICIAN VISIT                  4  ...            NaN   
3                  WELL CHECK                  x  ...            NaN   
4             CLINICIAN VISIT                  4  ...            NaN   
...                       ...                ...  ...            ...   
99995         CLINICIAN VISIT                  x  ...            NaN   
99996                  Annual                  x  ...            NaN   
99997  Established Sick Visit                  x  ...            NaN   
99998         CLINICIAN VISIT                  x  ...            NaN   
99999                 TELEMED                  x  ...            NaN   

      geocode_state geocode_stusab geocode_latitude  geocode_longitude  \
0               NaN            NaN              NaN                NaN   
1               NaN            NaN              NaN                NaN   
2               NaN            NaN              NaN                NaN   
3               NaN            NaN              NaN                NaN   
4               NaN            NaN              NaN                NaN   
...             ...            ...              ...                ...   
99995           NaN            NaN              NaN                NaN   
99996           NaN            NaN              NaN                NaN   
99997           NaN            NaN              NaN                NaN   
99998           NaN            NaN              NaN                NaN   
99999           NaN            NaN              NaN                NaN   

       geocode_lengthlife geocode_healthybehaviors geocode_clinicalcare  \
0                     NaN                      NaN                  NaN   
1                     NaN                      NaN                  NaN   
2                     NaN                      NaN                  NaN   
3                     NaN                      NaN                  NaN   
4                     NaN                      NaN                  NaN   
...                   ...                      ...                

In [13]:
y

0        N
1        N
2        N
3        N
4        N
        ..
99995    Y
99996    Y
99997    Y
99998    Y
99999    Y
Name: appointment_yosi_noshow1, Length: 100000, dtype: object

In [14]:
x_train, x_test, y_train, y_test = train_test_split(x, y, stratify=y, test_size=0.25)

In [15]:
x_test

id   patient_id_2  practice_id  appointment_id  patient_id  \
66850  1143205  325506_221709       325506         1563716      221709   
91585   206355    29501_61334        29501          205209       61334   
52282   735021  303801_582230       303801         2767606      582230   
62836  1333482  325510_244108       325510         1647977      244108   
89322  1367730  325510_419549       325510         3605088      419549   
...        ...            ...          ...             ...         ...   
98914  1109615  325505_100937       325505         2153748      100937   
79292   979133  325504_117141       325504          535633      117141   
95883   559254  303205_186833       303205         1821227      186833   
30042  1398171  325511_382744       325511         3149154      382744   
50505   899027  325502_227713       325502         2599700      227713   

      appointment_date appointment_start_time  appointment_duration  \
66850       2020-10-30               09:10:00                    10   
91585       2018-12-17               09:00:00                    20   
52282       2020-06-24               13:30:00                    15   
62836       2020-11-20               17:05:00                     5   
89322       2021-09-02               16:15:00                    10   
...                ...                    ...                   ...   
98914       2021-06-09               11:30:00                     5   
79292       2019-12-30               13:38:00                    10   
95883       2021-09-23               13:30:00                    15   
30042       2021-06-16               10:35:00                     5   
50505       2020-12-12               15:50:00                    10   

              appointment_type appointment_status  ... geocode_county  \
66850                  TELEMED                  x  ...            NaN   
91585         OFFICE VISIT NEW                  x  ...            NaN   
52282                  New GYN                  x  ...            NaN   
62836      Rapid-COVID Antigen                  x  ...            NaN   
89322      Rapid-COVID Antigen                  x  ...            NaN   
...                        ...                ...  ...            ...   
98914      Rapid-COVID Antigen                  x  ...            NaN   
79292              VACCINATION                  x  ...            NaN   
95883             New/Est Sick                  x  ...            NaN   
30042  Rapid-COVID PCR Cepheid                  4  ...            NaN   
50505          CLINICIAN VISIT                  x  ...            NaN   

      geocode_state geocode_stusab geocode_latitude  geocode_longitude  \
66850           NaN            NaN              NaN                NaN   
91585           NaN            NaN              NaN                NaN   
52282           NaN            NaN              NaN                NaN   
62836           NaN            NaN              NaN                NaN   
89322           NaN            NaN              NaN                NaN   
...             ...            ...              ...                ...   
98914           NaN            NaN              NaN                NaN   
79292           NaN            NaN              NaN                NaN   
95883           NaN            NaN              NaN                NaN   
30042           NaN            NaN              NaN                NaN   
50505           NaN            NaN              NaN                NaN   

       geocode_lengthlife geocode_healthybehaviors geocode_clinicalcare  \
66850                 NaN                      NaN                  NaN   
91585                 NaN                      NaN                  NaN   
52282                 NaN                      NaN                  NaN   
62836                 NaN                      NaN                  NaN   
89322                 NaN                      NaN                  NaN   
...                   ...                      ...    

In [16]:
automl = AutoML(results_path="df_no_show_test", mode="Explain")

In [17]:
automl.fit(x_train, y_train)

Linear algorithm was disabled.
AutoML directory: df_no_show_test
The task is binary_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 0.693147 trained in 1.3 seconds


2_DecisionTree logloss 0.11415 trained in 62.63 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.078474 trained in 147.92 seconds
4_Default_NeuralNetwork logloss 0.121126 trained in 209.5 seconds
5_Default_RandomForest logloss 0.110357 trained in 197.87 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.078474 trained in 4.09 seconds
AutoML fit time: 638.74 seconds
AutoML best model: 3_Default_Xgboost


AutoML(results_path='df_no_show_test')

In [18]:
pred = automl.predict(x_test)
pred

array(['Y', 'Y', 'Y', ..., 'Y', 'N', 'Y'], dtype=object)

In [19]:
automl.report()

outputs

In [20]:
import os
os.getcwd()

'/content'

In [21]:
folders = os.listdir()
foldersML = [x for x in folders if x.startswith('df')]
print(foldersML)

['df_no_show_test']


In [23]:
!zip -r /content/df_no_show_test/.zip /content/df_no_show_test/

  adding: content/df_no_show_test/ (stored 0%)
  adding: content/df_no_show_test/params.json (deflated 61%)
  adding: content/df_no_show_test/data_info.json (deflated 87%)
  adding: content/df_no_show_test/leaderboard.csv (deflated 42%)
  adding: content/df_no_show_test/1_Baseline/ (stored 0%)
  adding: content/df_no_show_test/1_Baseline/cumulative_gains_curve.png (deflated 7%)
  adding: content/df_no_show_test/1_Baseline/learner_fold_0_training.log (deflated 35%)
  adding: content/df_no_show_test/1_Baseline/confusion_matrix_normalized.png (deflated 21%)
  adding: content/df_no_show_test/1_Baseline/framework.json (deflated 71%)
  adding: content/df_no_show_test/1_Baseline/roc_curve.png (deflated 7%)
  adding: content/df_no_show_test/1_Baseline/precision_recall_curve.png (deflated 11%)
  adding: content/df_no_show_test/1_Baseline/calibration_curve_curve.png (deflated 13%)
  adding: content/df_no_show_test/1_Baseline/learner_fold_0.baseline (stored 0%)
  adding: content/df_no_show_test/1